# ML Pipeline Preparation
Follow the instructions below to help you create your ML pipeline.
### 1. Import libraries and load data from database.
- Import Python libraries
- Load dataset from database with [`read_sql_table`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_sql_table.html)
- Define feature and target variables X and Y

In [346]:
#import the nltk module
import nltk
nltk.download(['punkt', 'wordnet', 'averaged_perceptron_tagger', 'stopwords'])

[nltk_data] Downloading package punkt to /Users/padmaja/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/padmaja/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/padmaja/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/padmaja/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [347]:
# import libraries
import pandas as pd
import numpy as np
import re
import time
from sqlalchemy import create_engine
from nltk.corpus import wordnet, stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.multioutput import MultiOutputClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, f1_score, precision_score, accuracy_score
from sklearn.model_selection import GridSearchCV
from sklearn.neural_network import MLPClassifier
from skmultilearn.model_selection.iterative_stratification import iterative_train_test_split
from skmultilearn.model_selection import IterativeStratification
import pickle

In [371]:
# load data from database
engine = create_engine('sqlite:///../data/DisasterResponse.db')
df = pd.read_sql_table('disaster_response', engine)

#### Print the first few rows from the dataframe

In [372]:
df.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  related  \
0  Un front froid se retrouve sur Cuba ce matin. ...  direct        1   
1                 Cyclone nan fini osinon li pa fini  direct        1   
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct        1   
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct        1   
4  facade ouest d Haiti et le reste du pays aujou...  direct        1   

   request  offer  aid_related  medical_help  medical_products  ...  \
0        0      0            0             0                 0  ...   
1        0      0            1             0                 0  ...   
2        0      0            0             0                 0  ...   
3        1      0            1             0                 1  ...   
4        0      0            0             0                 0  ...   

   aid_centers  other_infrastructure  weather_related  floods  storm  fire  \
0            0                     0                0       0      0     0   
1            0                     0                1       0      1     0   
2            0                     0                0       0      0     0   
3            0                     0                0       0      0     0   
4            0                     0                0       0      0     0   

   earthquake  cold  other_weather  direct_report  
0           0     0              0              0  
1           0     0              0              0  
2           0     0              0              0  
3           0     0              0              0  
4           0     0              0              0  

[5 rows x 40 columns]

#### Lets check  if there are any columns with null values

In [373]:
df.dtypes

id                         int64
message                   object
original                  object
genre                     object
related                    int64
request                    int64
offer                      int64
aid_related                int64
medical_help               int64
medical_products           int64
search_and_rescue          int64
security                   int64
military                   int64
child_alone                int64
water                      int64
food                       int64
shelter                    int64
clothing                   int64
money                      int64
missing_people             int64
refugees                   int64
death                      int64
other_aid                  int64
infrastructure_related     int64
transport                  int64
buildings                  int64
electricity                int64
tools                      int64
hospitals                  int64
shops                      int64
aid_center

In [374]:
df.isnull().sum()

id                            0
message                       0
original                  16027
genre                         0
related                       0
request                       0
offer                         0
aid_related                   0
medical_help                  0
medical_products              0
search_and_rescue             0
security                      0
military                      0
child_alone                   0
water                         0
food                          0
shelter                       0
clothing                      0
money                         0
missing_people                0
refugees                      0
death                         0
other_aid                     0
infrastructure_related        0
transport                     0
buildings                     0
electricity                   0
tools                         0
hospitals                     0
shops                         0
aid_centers                   0
other_in

We see that none of the target categories have missing values.

In [376]:
target_cols = list(df.select_dtypes(include='int64').columns)

In [377]:
target_cols.remove('id')

#### Lets check how many classes exist for each of the target categories

In [363]:
for col in target_cols:
    display(df[col].value_counts())

1    20064
0     6116
Name: related, dtype: int64

0    21716
1     4464
Name: request, dtype: int64

0    26062
1      118
Name: offer, dtype: int64

0    15339
1    10841
Name: aid_related, dtype: int64

0    24099
1     2081
Name: medical_help, dtype: int64

...

0    25898
1      282
Name: fire, dtype: int64

0    23728
1     2452
Name: earthquake, dtype: int64

0    25652
1      528
Name: cold, dtype: int64

0    24804
1     1376
Name: other_weather, dtype: int64

0    21116
1     5064
Name: direct_report, dtype: int64

We see that the 'child_alone' category has only one class (0).<BR>
We will delete the 'child_alone' category

In [378]:
df.drop(columns='child_alone', inplace=True)

In [380]:
target_cols.remove('child_alone')

In [381]:
target_cols

['related',
 'request',
 'offer',
 'aid_related',
 'medical_help',
 'medical_products',
 'search_and_rescue',
 'security',
 'military',
 'water',
 'food',
 'shelter',
 'clothing',
 'money',
 'missing_people',
 'refugees',
 'death',
 'other_aid',
 'infrastructure_related',
 'transport',
 'buildings',
 'electricity',
 'tools',
 'hospitals',
 'shops',
 'aid_centers',
 'other_infrastructure',
 'weather_related',
 'floods',
 'storm',
 'fire',
 'earthquake',
 'cold',
 'other_weather',
 'direct_report']

In [382]:
#Define the feature and target variables
X = df['message'].values
Y = df[target_cols].values

In [383]:
display(X.shape); display(Y.shape)

(26180,)

(26180, 35)

### 2. Write a tokenization function to process your text data

In [384]:
def tokenize(text):
    # Normalize text
    text = text.lower()
    
    # Tokenize text
    tokens = word_tokenize(text)

    lemmatizer = WordNetLemmatizer()

    clean_tokens = []
    for tok in tokens:
        clean_tok = lemmatizer.lemmatize(tok, pos='v').strip()
        clean_tokens.append(clean_tok)

    return clean_tokens

### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [18]:
pipeline = Pipeline([
       ('vect', CountVectorizer(tokenizer=tokenize)),
       ('tfidf', TfidfTransformer()),
       ('clf', MultiOutputClassifier(RandomForestClassifier(verbose=2))),
    ]) 

### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [19]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, random_state=42, test_size=0.3)

display(X_train.shape); display(Y_train.shape)
display(X_train[0:5])


(18229,)

(18229, 35)

array(['Operation USA would like to thank all those who have generously donated to recovery efforts so far.',
       '(word missing, I assume it is information) on the job market ',
       "26/05/2015 - Moneragala, Sri Lanka: The Sri Lanka Red Cross Society's Moneragala Branch has taken adequate steps to provide water & sanitation support to over 500 families within the district who are in the drought stricken area of the district.",
       'You are registered as an SOS message recipient ',
       'The UN Country Team continues to undertake daily sectoral meetings (health, water and sanitation) with the relevant Government authorities.'],
      dtype=object)

In [20]:
display(X_train[15:20])
display(Y_train[15:20])

array(['Vehicular traffic on the Hyderabad-Kurnool route is stuck at Beechpalli on National Highway 7 while the services of APSRTC as well as private road transport agencies has been paralysed.',
       'Working with partners in healthcare, health departments will: - Perform targeted assessments of infection control competency at healthcare facilities; - Identify gaps in infection control performance and facilitate/implement programs and policies to address these gaps; and - Implement response and prevention activities aimed at making a large impact on reducing transmission of pathogens in healthcare settings.',
       "LONDON, Dec 29 (Reuters) - The United Nations mobilised what it called the biggest relief operation in its history following Sunday's giant wave which killed tens of thousands of people.",
       "My house is brocken,I don't have tent. ",
       "573,624 Power outages in New Jersey and counting! #FuckYouSandyCan't stop sneezing. Clearly allergic to hurricanes. #sandy"],

array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.],
       [1., 0., 0., 1., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.],
       [1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1.,
        0., 0., 0.],
       [1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.],
       [1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0.,
        0., 0., 1.]])

In [237]:
display(time.time())
pipeline.fit(X_train, Y_train)
display(time.time())

1646692352.294105

1646692948.055626

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

In [238]:
display(time.time())
Y_pred = pipeline.predict(X_test)
display(time.time())

1646692948.062659

1646693026.5767019

In [250]:
for i in range(len(target_cols)):
    cr = classification_report(Y_test[:,i], Y_pred[:,i], zero_division=1)
    print(target_cols[i])
    print(cr)

related
              precision    recall  f1-score   support

         0.0       0.39      0.04      0.07      1873
         1.0       0.76      0.98      0.86      5940

    accuracy                           0.75      7813
   macro avg       0.58      0.51      0.46      7813
weighted avg       0.67      0.75      0.67      7813

request
              precision    recall  f1-score   support

         0.0       0.83      0.99      0.90      6442
         1.0       0.47      0.03      0.06      1371

    accuracy                           0.82      7813
   macro avg       0.65      0.51      0.48      7813
weighted avg       0.76      0.82      0.76      7813

offer
              precision    recall  f1-score   support

         0.0       0.99      1.00      1.00      7773
         1.0       1.00      0.00      0.00        40

    accuracy                           0.99      7813
   macro avg       1.00      0.50      0.50      7813
weighted avg       0.99      0.99      0.99      781

floods
              precision    recall  f1-score   support

         0.0       0.92      1.00      0.96      7151
         1.0       0.25      0.00      0.01       662

    accuracy                           0.91      7813
   macro avg       0.58      0.50      0.48      7813
weighted avg       0.86      0.91      0.88      7813

storm
              precision    recall  f1-score   support

         0.0       0.91      1.00      0.95      7099
         1.0       0.33      0.02      0.03       714

    accuracy                           0.91      7813
   macro avg       0.62      0.51      0.49      7813
weighted avg       0.86      0.91      0.87      7813

fire
              precision    recall  f1-score   support

         0.0       0.99      1.00      0.99      7726
         1.0       1.00      0.00      0.00        87

    accuracy                           0.99      7813
   macro avg       0.99      0.50      0.50      7813
weighted avg       0.99      0.99      0.98      7813

e

### 6. Improve your model
Use grid search to find better parameters. 

In [271]:
pipeline.get_params().keys()

dict_keys(['memory', 'steps', 'verbose', 'vect', 'tfidf', 'clf', 'vect__analyzer', 'vect__binary', 'vect__decode_error', 'vect__dtype', 'vect__encoding', 'vect__input', 'vect__lowercase', 'vect__max_df', 'vect__max_features', 'vect__min_df', 'vect__ngram_range', 'vect__preprocessor', 'vect__stop_words', 'vect__strip_accents', 'vect__token_pattern', 'vect__tokenizer', 'vect__vocabulary', 'tfidf__norm', 'tfidf__smooth_idf', 'tfidf__sublinear_tf', 'tfidf__use_idf', 'clf__estimator__bootstrap', 'clf__estimator__ccp_alpha', 'clf__estimator__class_weight', 'clf__estimator__criterion', 'clf__estimator__max_depth', 'clf__estimator__max_features', 'clf__estimator__max_leaf_nodes', 'clf__estimator__max_samples', 'clf__estimator__min_impurity_decrease', 'clf__estimator__min_impurity_split', 'clf__estimator__min_samples_leaf', 'clf__estimator__min_samples_split', 'clf__estimator__min_weight_fraction_leaf', 'clf__estimator__n_estimators', 'clf__estimator__n_jobs', 'clf__estimator__oob_score', 'clf_

In [272]:
parameters = {
        'vect__ngram_range': ((1, 1), (1, 2)),
        'clf__estimator__n_estimators': [50, 100, 200]
    }
cv = GridSearchCV(pipeline, param_grid=parameters, n_jobs=-1)

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

In [273]:
display(time.time())
cv.fit(X_train, Y_train)
display(time.time())

1646695194.696068

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.6s remaining:    0.0s
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Using backe

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   20.5s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   20.7s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   12.9s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   12.8s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent work

[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   30.4s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   30.8s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   30.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:    8.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:    8.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Para

[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   44.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.5s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.8s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   44.3s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.6s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   44.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:   24.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.4s remaining:    0

...

building tree 1 of 200


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s


building tree 2 of 200
building tree 3 of 200
building tree 4 of 200
building tree 5 of 200
building tree 6 of 200
building tree 7 of 200
building tree 8 of 200
building tree 9 of 200
building tree 10 of 200
building tree 11 of 200
building tree 12 of 200
building tree 13 of 200
building tree 14 of 200
building tree 15 of 200
building tree 16 of 200
building tree 17 of 200
building tree 18 of 200
building tree 19 of 200
building tree 20 of 200
building tree 21 of 200
building tree 22 of 200
building tree 23 of 200
building tree 24 of 200
building tree 25 of 200
building tree 26 of 200
building tree 27 of 200
building tree 28 of 200
building tree 29 of 200
building tree 30 of 200
building tree 31 of 200
building tree 32 of 200
building tree 33 of 200
building tree 34 of 200
building tree 35 of 200
building tree 36 of 200
building tree 37 of 200
building tree 38 of 200
building tree 39 of 200
building tree 40 of 200
building tree 41 of 200
building tree 42 of 200
building tree 43 of 200


[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:   46.9s finished


1646707451.18865

In [274]:
cv.best_params_

{'clf__estimator__n_estimators': 200, 'vect__ngram_range': (1, 1)}

In [275]:
display(time.time())
Y_pred = cv.predict(X_test)
display(time.time())

1646708182.549498

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    2.8s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    1.9s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    0.6s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    2.6s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent work

1646708262.3024268

In [276]:
for i in range(len(target_cols)):
    cr = classification_report(Y_test[:,i], Y_pred[:,i], zero_division=1)
    print(target_cols[i])
    print(cr)

related
              precision    recall  f1-score   support

         0.0       0.45      0.02      0.03      1873
         1.0       0.76      0.99      0.86      5940

    accuracy                           0.76      7813
   macro avg       0.61      0.51      0.45      7813
weighted avg       0.69      0.76      0.66      7813

request
              precision    recall  f1-score   support

         0.0       0.83      1.00      0.90      6442
         1.0       0.43      0.01      0.03      1371

    accuracy                           0.82      7813
   macro avg       0.63      0.51      0.47      7813
weighted avg       0.76      0.82      0.75      7813

offer
              precision    recall  f1-score   support

         0.0       0.99      1.00      1.00      7773
         1.0       1.00      0.00      0.00        40

    accuracy                           0.99      7813
   macro avg       1.00      0.50      0.50      7813
weighted avg       0.99      0.99      0.99      781

floods
              precision    recall  f1-score   support

         0.0       0.92      1.00      0.96      7151
         1.0       0.60      0.00      0.01       662

    accuracy                           0.92      7813
   macro avg       0.76      0.50      0.48      7813
weighted avg       0.89      0.92      0.88      7813

storm
              precision    recall  f1-score   support

         0.0       0.91      1.00      0.95      7099
         1.0       0.38      0.01      0.02       714

    accuracy                           0.91      7813
   macro avg       0.64      0.50      0.48      7813
weighted avg       0.86      0.91      0.87      7813

fire
              precision    recall  f1-score   support

         0.0       0.99      1.00      0.99      7726
         1.0       1.00      0.00      0.00        87

    accuracy                           0.99      7813
   macro avg       0.99      0.50      0.50      7813
weighted avg       0.99      0.99      0.98      7813

e

In [279]:
best_model = cv.best_estimator_

In [280]:
display(time.time())
Y_pred = best_model.predict(X_test)
display(time.time())

1646708998.8262022

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    2.3s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    1.5s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    0.5s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 200 out of 200 | elapsed:    2.5s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent work

1646709100.759943

In [281]:
for i in range(len(target_cols)):
    cr = classification_report(Y_test[:,i], Y_pred[:,i], zero_division=1)
    print(target_cols[i])
    print(cr)

related
              precision    recall  f1-score   support

         0.0       0.45      0.02      0.03      1873
         1.0       0.76      0.99      0.86      5940

    accuracy                           0.76      7813
   macro avg       0.61      0.51      0.45      7813
weighted avg       0.69      0.76      0.66      7813

request
              precision    recall  f1-score   support

         0.0       0.83      1.00      0.90      6442
         1.0       0.43      0.01      0.03      1371

    accuracy                           0.82      7813
   macro avg       0.63      0.51      0.47      7813
weighted avg       0.76      0.82      0.75      7813

offer
              precision    recall  f1-score   support

         0.0       0.99      1.00      1.00      7773
         1.0       1.00      0.00      0.00        40

    accuracy                           0.99      7813
   macro avg       1.00      0.50      0.50      7813
weighted avg       0.99      0.99      0.99      781

floods
              precision    recall  f1-score   support

         0.0       0.92      1.00      0.96      7151
         1.0       0.60      0.00      0.01       662

    accuracy                           0.92      7813
   macro avg       0.76      0.50      0.48      7813
weighted avg       0.89      0.92      0.88      7813

storm
              precision    recall  f1-score   support

         0.0       0.91      1.00      0.95      7099
         1.0       0.38      0.01      0.02       714

    accuracy                           0.91      7813
   macro avg       0.64      0.50      0.48      7813
weighted avg       0.86      0.91      0.87      7813

fire
              precision    recall  f1-score   support

         0.0       0.99      1.00      0.99      7726
         1.0       1.00      0.00      0.00        87

    accuracy                           0.99      7813
   macro avg       0.99      0.50      0.50      7813
weighted avg       0.99      0.99      0.98      7813

e

### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

#### Create a StartingVerbExtracter class to identify if the first word of a sentence is a verb, and return True if it is a verb.
#### The StartingVerbExtracter will be used as an additional step in the Pipeline object to extract this additional feature.

In [385]:
class StartingVerbExtractor(BaseEstimator, TransformerMixin):

    def starting_verb(self, text):
        sentence_list = nltk.sent_tokenize(text)
        for sentence in sentence_list:
            pos_tags = nltk.pos_tag(tokenize(sentence))
            first_word, first_tag = pos_tags[0]
            if first_tag in ['VB', 'VBP'] or first_word == 'RT':
                return True
        return False

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X_tagged = pd.Series(X).apply(self.starting_verb)
        return pd.DataFrame(X_tagged)

###### We will use the iterative_train_test_split method from the skmultilearn.model_selection to perform a stratified sampling of the multi-labeled data

In [386]:
X_train1, Y_train1, X_test1, Y_test1 = iterative_train_test_split(
    df[["message"]].values,
    df[target_cols].values,
    test_size = 0.3
)

In [387]:
X_train1 = X_train1.flatten()
X_test1 = X_test1.flatten()

##### We will use the IterativeStratification method from the skmultilearn.model_selection to perform a stratified sampling when creating the k-folds during cross-validation.

In [389]:
k_fold = IterativeStratification(n_splits=3, order=1)

In [390]:
pipeline2 = Pipeline([
    ('features', FeatureUnion([

        ('nlp_pipeline', Pipeline([
            ('vect', CountVectorizer(tokenizer=tokenize)),
            ('tfidf', TfidfTransformer())]
        )),

        ('start_verb', StartingVerbExtractor())
     ])),
        
        ('clf', MLPClassifier(max_iter=300, random_state=42, verbose=True))
    ])

In [391]:
parameters = {
        'clf__hidden_layer_sizes': [(30,), (50,)]
    }
grid_cv = GridSearchCV(pipeline2, param_grid=parameters, scoring='f1_weighted', cv=k_fold, n_jobs=-1)

In [392]:
display(time.time())
grid_cv.fit(X_train1, Y_train1)
display(time.time())

1647296799.1539881

/Users/padmaja/opt/anaconda3/lib/python3.9/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (300) reached and the optimization hasn't converged yet.
  warnings.warn(
/Users/padmaja/opt/anaconda3/lib/python3.9/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (300) reached and the optimization hasn't converged yet.
  warnings.warn(
/Users/padmaja/opt/anaconda3/lib/python3.9/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (300) reached and the optimization hasn't converged yet.
  warnings.warn(


Iteration 1, loss = 22.72647927
Iteration 2, loss = 13.92926132
Iteration 3, loss = 9.31978596
Iteration 4, loss = 8.43665240
Iteration 5, loss = 8.07054460
Iteration 6, loss = 7.78551272
Iteration 7, loss = 7.51476832
Iteration 8, loss = 7.18644452
Iteration 9, loss = 6.85859650
Iteration 10, loss = 6.57199406
Iteration 11, loss = 6.32531356
Iteration 12, loss = 6.11072083
Iteration 13, loss = 5.90828408
Iteration 14, loss = 5.70534319
Iteration 15, loss = 5.49381977
Iteration 16, loss = 5.28369579
Iteration 17, loss = 5.07808098
Iteration 18, loss = 4.88188051
Iteration 19, loss = 4.69824336
Iteration 20, loss = 4.52710098
Iteration 21, loss = 4.36886264
Iteration 22, loss = 4.22115716
Iteration 23, loss = 4.08263568
Iteration 24, loss = 3.95035057
Iteration 25, loss = 3.82531777
Iteration 26, loss = 3.70660533
Iteration 27, loss = 3.59220202
Iteration 28, loss = 3.48172925
Iteration 29, loss = 3.37491304
Iteration 30, loss = 3.27295334
Iteration 31, loss = 3.17441787
Iteration 32, l

Iteration 276, loss = 0.06129654
Iteration 277, loss = 0.06110602
Iteration 278, loss = 0.06087845
Iteration 279, loss = 0.06046432
Iteration 280, loss = 0.06048153
Iteration 281, loss = 0.06006223
Iteration 282, loss = 0.05977855
Iteration 283, loss = 0.05962549
Iteration 284, loss = 0.05920126
Iteration 285, loss = 0.05884696
Iteration 286, loss = 0.05857589
Iteration 287, loss = 0.05840046
Iteration 288, loss = 0.05837261
Iteration 289, loss = 0.05797214
Iteration 290, loss = 0.05772738
Iteration 291, loss = 0.05769237
Iteration 292, loss = 0.05752354
Iteration 293, loss = 0.05694774
Iteration 294, loss = 0.05697950
Iteration 295, loss = 0.05651312
Iteration 296, loss = 0.05624784
Iteration 297, loss = 0.05586975
Iteration 298, loss = 0.05596230
Iteration 299, loss = 0.05576302
Iteration 300, loss = 0.05516372
Iteration 1, loss = 22.12538453
Iteration 2, loss = 14.06322796
Iteration 3, loss = 9.33013057
Iteration 4, loss = 8.28321127
Iteration 5, loss = 7.82399277
Iteration 6, loss 

/Users/padmaja/opt/anaconda3/lib/python3.9/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (300) reached and the optimization hasn't converged yet.
  warnings.warn(


...

Iteration 15, loss = 3.78213208
Iteration 16, loss = 3.60409679
Iteration 17, loss = 3.43408297
Iteration 18, loss = 3.27321133
Iteration 19, loss = 3.11942982
Iteration 20, loss = 2.97294352
Iteration 21, loss = 2.83262127
Iteration 22, loss = 2.69885602
Iteration 23, loss = 2.57134645
Iteration 24, loss = 2.45031012
Iteration 25, loss = 2.33400878
Iteration 26, loss = 2.22442746
Iteration 27, loss = 2.11901969
Iteration 28, loss = 2.01994455
Iteration 29, loss = 1.92606494
Iteration 30, loss = 1.83678509
Iteration 31, loss = 1.75150757
Iteration 32, loss = 1.67117855
Iteration 33, loss = 1.59504219
Iteration 34, loss = 1.52223939
Iteration 35, loss = 1.45417169
Iteration 36, loss = 1.38889378
Iteration 1, loss = 21.56658468
Iteration 2, loss = 11.66028021
Iteration 3, loss = 8.58266369
Iteration 4, loss = 7.98331474
Iteration 5, loss = 7.52965541
Iteration 6, loss = 7.09783709
Iteration 7, loss = 6.71199830
Iteration 8, loss = 6.36354653
Iteration 9, loss = 6.04001781
Iteration 10, l

Iteration 37, loss = 1.32789862
Iteration 38, loss = 1.26980578
Iteration 39, loss = 1.21413842
Iteration 40, loss = 1.16230851
Iteration 41, loss = 1.11219992
Iteration 42, loss = 1.06541643
Iteration 43, loss = 1.02059170
Iteration 44, loss = 0.97830997
Iteration 45, loss = 0.93820693
Iteration 46, loss = 0.89982331
Iteration 47, loss = 0.86457452
Iteration 48, loss = 0.82997733
Iteration 49, loss = 0.79740440
Iteration 50, loss = 0.76666348
Iteration 51, loss = 0.73694289
Iteration 52, loss = 0.70896939
Iteration 53, loss = 0.68274280
Iteration 54, loss = 0.65749059
Iteration 55, loss = 0.63403719
Iteration 56, loss = 0.61142043
Iteration 57, loss = 0.58916270
Iteration 58, loss = 0.56873980
Iteration 59, loss = 0.54963160
Iteration 60, loss = 0.53000377
Iteration 61, loss = 0.51305077
Iteration 62, loss = 0.49566883
Iteration 63, loss = 0.47963846
Iteration 64, loss = 0.46385261
Iteration 65, loss = 0.44947780
Iteration 66, loss = 0.43565321
Iteration 67, loss = 0.42221674
Iteratio

Iteration 288, loss = 0.05231162
Iteration 289, loss = 0.05208351
Iteration 290, loss = 0.05157184
Iteration 291, loss = 0.05141164
Iteration 292, loss = 0.05137902
Iteration 293, loss = 0.05095769
Iteration 294, loss = 0.05078958
Iteration 295, loss = 0.05073039
Iteration 296, loss = 0.05050882
Iteration 297, loss = 0.05066744
Iteration 298, loss = 0.05012221
Iteration 299, loss = 0.04999411
Iteration 300, loss = 0.04992726


/Users/padmaja/opt/anaconda3/lib/python3.9/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (300) reached and the optimization hasn't converged yet.
  warnings.warn(


1647302230.933328

In [393]:
model = grid_cv.best_estimator_
grid_cv.best_params_

{'clf__hidden_layer_sizes': (50,)}

In [394]:
display(time.time())
Y_pred1 = model.predict(X_test1)
display(time.time())

1647302371.55217

1647302389.903027

##### Report the f1 score, precision and recall for each output category of the dataset. We will do this by iterating through the columns and calling sklearn's classification_report on each.

In [395]:
for i in range(len(target_cols)):
    cr = classification_report(Y_test1[:,i], Y_pred1[:,i], zero_division=1)
    print(target_cols[i])
    print(cr)

related
              precision    recall  f1-score   support

           0       0.45      0.43      0.44      1835
           1       0.83      0.84      0.84      6019

    accuracy                           0.75      7854
   macro avg       0.64      0.64      0.64      7854
weighted avg       0.74      0.75      0.74      7854

request
              precision    recall  f1-score   support

           0       0.88      0.90      0.89      5993
           1       0.65      0.62      0.64      1861

    accuracy                           0.83      7854
   macro avg       0.77      0.76      0.76      7854
weighted avg       0.83      0.83      0.83      7854

offer
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      7819
           1       0.00      0.00      0.00        35

    accuracy                           0.99      7854
   macro avg       0.50      0.50      0.50      7854
weighted avg       0.99      0.99      0.99      785

fire
              precision    recall  f1-score   support

           0       0.99      1.00      1.00      7771
           1       0.64      0.25      0.36        83

    accuracy                           0.99      7854
   macro avg       0.81      0.63      0.68      7854
weighted avg       0.99      0.99      0.99      7854

earthquake
              precision    recall  f1-score   support

           0       0.96      0.97      0.97      6909
           1       0.78      0.71      0.74       945

    accuracy                           0.94      7854
   macro avg       0.87      0.84      0.85      7854
weighted avg       0.94      0.94      0.94      7854

cold
              precision    recall  f1-score   support

           0       0.99      0.99      0.99      7696
           1       0.55      0.35      0.43       158

    accuracy                           0.98      7854
   macro avg       0.77      0.67      0.71      7854
weighted avg       0.98      0.98      0.98      7854

### 9. Export your model as a pickle file

In [397]:
pkl_filename = "../models/model_classifier.pkl"
with open(pkl_filename, 'wb') as file:
    pickle.dump(model, file)

### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.